In [1]:
import tempfile
import plotly.express as px
import pandas as pd
from lib.integrated_single_scenario import Scenario, BaseScenario
import shutil
import os
import numpy as np
from pathlib import Path

c:\Users\szvsw\repos\mit-campus-decarbonization\lib\integrated_single_scenario.py:14: TqdmExperimentalWarning: Using `tqdm.autonotebook.tqdm` in notebook mode. Use `tqdm.tqdm` instead to force console mode (e.g. in jupyter console)
  from tqdm.autonotebook import tqdm


In [2]:
base_ix = 0
batch = "cc9e9cff-64f0-4fbf-b17a-2f829837f896" # with our labs, but no upgrades
batch = "fd346eec-ef8b-4a06-a006-5a219c9246c4"  # with amanda's labs
# batch = "976d9f9a-c11d-49d2-b765-acf8e65c2897" # with edited amanda's labs, baseline only
batch = "ca9aa8a5-d7a9-4dcb-819f-2b573df3d037" # new baseline 04/19
batch = "ab8a082c-6c94-4e7f-a5ff-e6a1be042879" # new baseline 04/20
batch = "f0ba4a9e-40de-4545-8f34-781abbd7f9ae" # new baseline 04/20 - higher lab cfm 0.1/0.1/none - lower dhw
batch = "557fa793-bf11-4e8f-a504-440e3542e801" # new baseline 04/20 - higher lab cfm 0/0.03249/none - lower dhw
batch = "e89b3918-c6d6-46a0-ba0e-0bedc4287a23" # new baseline 04/20 - higher lab cfm 0.015/0.015/none - lower dhw
profiles_path = f"sdl-epengine/dev/{batch[:8]}/results"

scenarios_df = BaseScenario.make_df()

dfs = []
with tempfile.TemporaryDirectory() as artifacts_dir:
    # base_scenario: BaseScenario = scenarios_df.iloc[base_ix].Scenario
    for dg in ["baseline"]:
        base_scenario = BaseScenario(
            renorate="fast",
            climate="rcp45",
            grid="decarbonization",
            retrofit="baseline",
            schedules="baseline",
            lab="baseline",
            district="baseline",
            nuclear="baseline",
            deepgeo=dg,
            ess="baseline",
            ccs="baseline"
        )
        s = Scenario(
            artifacts_dir=artifacts_dir,
            profiles_path=profiles_path,
            x=base_scenario,
        )
        tl: pd.DataFrame = s.run()
        k: pd.DataFrame = tl.Emissions.groupby("epw_year").sum()
        k = k.rename(columns={"Total":"Emissions"})
        k["Innovation"] = 15
        k["Risk"] = 10
        k = k[["Emissions","Innovation","Risk"]]
        ix = base_scenario.to_index()
        k = k.set_index(ix.repeat(len(k)), append=True)
        dfs.append(k)

df = pd.concat(dfs)


INTEGRATED:INFO: ----
INTEGRATED:INFO: 
Scenario:
	climate=rcp45
	grid=decarbonization
	retrofit=baseline
	schedules=baseline
	lab=baseline
	district=baseline
	nuclear=baseline
	deepgeo=baseline
	renorate=fast
	ess=baseline
	ccs=baseline
INTEGRATED:DEBUG: Fetching files from ml-for-bem/sdl-epengine/dev/557fa793/results
INTEGRATED:DEBUG: Found 512 files in sdl-epengine/dev/557fa793/results
INTEGRATED:DEBUG: Found 512 source files and 512 target files
INTEGRATED:DEBUG: Downloading artifacts...


Opening source HDFs:   0%|          | 0/512 [00:00<?, ?it/s]

Opening target HDFs:   0%|          | 0/512 [00:00<?, ?it/s]

INTEGRATED:DEBUG: Finished downloading and opening artifacts.
INTEGRATED:DEBUG: Concatenating artifacts...
INTEGRATED:INFO: Finished loading artifacts.
INTEGRATED:DEBUG: Making load sequence...
INTEGRATED:INFO: Finished making load sequence.
INTEGRATED:DEBUG: Generating district phase assignments...
INTEGRATED:DEBUG: Done generating district phase assignments.
INTEGRATED:DEBUG: Generating clean capacity...
INTEGRATED:WARNING: NO PV DATA AVAILABLE YET
INTEGRATED:WARNING: DEEP GEOTHERMAL THERMAAL CAPACITY NEEDS FINALIZING
INTEGRATED:DEBUG: Done generating clean capacity.
INTEGRATED:WARNING: NO GRID ARBITRAGE SCENARIO
INTEGRATED:WARNING: CARBON CAPTURE SCENARIOS NEEDS FINALIZING
INTEGRATED:WARNING: ESS SCENARIOS NEEDS FINALIZING
INTEGRATED:WARNING: DEEP GEOTHERMAL SCENARIOS NEEDS FINALIZING
INTEGRATED:WARNING: SCHEDULES PARTIAL needs finalizing
INTEGRATED:WARNING: VEHICLE LOADS NEEDED
INTEGRATED:WARNING: CHANGE CHILLER COPs
INTEGRATED:WARNING: NOT USING SURPLUS CLEAN
INTEGRATED:WARNING: C

In [3]:
annual = tl.groupby(level="epw_year").sum()
for lev in annual.columns.get_level_values(0).unique():
    fig = px.bar(
        annual[lev]
        .melt(ignore_index=False)
        .reset_index()
        .sort_values(["epw_year", "variable"]),
        x="epw_year",
        y="value",
        color="variable",
        title=lev,
    )
    fig.show()

c:\tools\Anaconda3\envs\mit-campus-decarbonization\lib\site-packages\plotly\express\_core.py:2065: FutureWarning: When grouping with a length-1 list-like, you will need to pass a length-1 tuple to get_group in a future version of pandas. Pass `(name,)` instead of `name` to silence this warning.
  sf: grouped.get_group(s if len(s) > 1 else s[0])


c:\tools\Anaconda3\envs\mit-campus-decarbonization\lib\site-packages\plotly\express\_core.py:2065: FutureWarning:

When grouping with a length-1 list-like, you will need to pass a length-1 tuple to get_group in a future version of pandas. Pass `(name,)` instead of `name` to silence this warning.



c:\tools\Anaconda3\envs\mit-campus-decarbonization\lib\site-packages\plotly\express\_core.py:2065: FutureWarning:

When grouping with a length-1 list-like, you will need to pass a length-1 tuple to get_group in a future version of pandas. Pass `(name,)` instead of `name` to silence this warning.



c:\tools\Anaconda3\envs\mit-campus-decarbonization\lib\site-packages\plotly\express\_core.py:2065: FutureWarning:

When grouping with a length-1 list-like, you will need to pass a length-1 tuple to get_group in a future version of pandas. Pass `(name,)` instead of `name` to silence this warning.



c:\tools\Anaconda3\envs\mit-campus-decarbonization\lib\site-packages\plotly\express\_core.py:2065: FutureWarning:

When grouping with a length-1 list-like, you will need to pass a length-1 tuple to get_group in a future version of pandas. Pass `(name,)` instead of `name` to silence this warning.



c:\tools\Anaconda3\envs\mit-campus-decarbonization\lib\site-packages\plotly\express\_core.py:2065: FutureWarning:

When grouping with a length-1 list-like, you will need to pass a length-1 tuple to get_group in a future version of pandas. Pass `(name,)` instead of `name` to silence this warning.



c:\tools\Anaconda3\envs\mit-campus-decarbonization\lib\site-packages\plotly\express\_core.py:2065: FutureWarning:

When grouping with a length-1 list-like, you will need to pass a length-1 tuple to get_group in a future version of pandas. Pass `(name,)` instead of `name` to silence this warning.



c:\tools\Anaconda3\envs\mit-campus-decarbonization\lib\site-packages\plotly\express\_core.py:2065: FutureWarning:

When grouping with a length-1 list-like, you will need to pass a length-1 tuple to get_group in a future version of pandas. Pass `(name,)` instead of `name` to silence this warning.



In [61]:
s.source_df.xs(2025,level="epw_year").to_hdf("2025_baseline.hdf", key="data")



In [54]:
k = s.source_df.xs(2025,level="epw_year").sum().Heating.argmax()
timestep = s.source_df.xs(2025,level="epw_year").sum().iloc[k+6::8760]




             DateTime           
Electricity  2018-01-15 12:00:00    36969.002111
Heating      2018-01-15 12:00:00    48677.307651
Cooling      2018-01-15 12:00:00     1427.577682
Water        2018-01-15 12:00:00     5616.306725
dtype: float64

In [40]:
Btu_per_Wh = 3.412
lb_per_Btu = 1/ 1199
kg_per_lb = 1  /  2.2
elec_coeff_kg_per_MW =613 * kg_per_lb
heating_coeff_kg_per_klb = 159 * kg_per_lb
# energy pool
energypool_total_cooling_MMBtu = 700e3
energypool_total_heating_MMBtu = 937e3
energypool_total_elec_MMBtu = 600e3
energypool_total_cooling_MWh = energypool_total_cooling_MMBtu / 3.412
energypool_total_heating_MWh = energypool_total_heating_MMBtu / 3.412
energypool_total_elec_MWh = energypool_total_elec_MMBtu / 3.412
# modeled
modeled_heating_MWh = 154e3
modeled_elec_MWh = 286e3
modeled_cooling_MWh = 102e3

#select
aggregate_heating_MWh = energypool_total_heating_MWh
aggregate_elec_MWh = energypool_total_elec_MWh
aggregate_cooling_MWh = energypool_total_cooling_MWh

# compute
base_cooling_load_MW = aggregate_cooling_MWh / 8760
base_elec_load_MW = aggregate_elec_MWh / 8760 +   base_cooling_load_MW/ 2 / 3.5
base_heating_load_MW = aggregate_heating_MWh / 8760 +  base_cooling_load_MW / 2 / 1.8
base_heating_load_kpph = base_heating_load_MW * Btu_per_Wh * lb_per_Btu * 1000 
elec_emissions_MT = base_elec_load_MW * elec_coeff_kg_per_MW * 8760 / 1000
heating_emissions_MT = base_heating_load_kpph * heating_coeff_kg_per_klb  * 8760 /1000
heating_emissions_MT + elec_emissions_MT








125365.19991866231

In [9]:
source = s.source_df.xs("62", level="building_id").xs(2025,level="epw_year")
source = source/source.index.get_level_values("actual_area").values[0]
target = s.source_df.xs("NW13", level="building_id").xs(2025,level="epw_year")
target = target/target.index.get_level_values("actual_area").values[0]
source.columns.names = ["end_use", "DateTime"]
target.columns.names = ["end_use", "DateTime"]
df = pd.concat([source, target], axis=0, keys=["left","right"], names=["which"])

# f = px.line(df.melt(ignore_index=False).reset_index(), x="DateTime", y="value", color="end_use", line_dash="which")
# # ff = px.line(target.melt(ignore_index=False).reset_index(), x="DateTime", y="value", color="end_use")
# # f.add_traces(ff.data)
# f.show()
df.T.groupby(level="end_use").sum()



which                                                                                       left  \
epw_scenario                                                                               rcp45   
retrofit_scenario                                                                       baseline   
schedules_scenario                                                                      baseline   
lab_scenario                                                                            baseline   
results_remote_path         EPW.rcp45_YR.2025_BLDG.62_RETRO.baseline_SCHED.baseline_LAB.baseline   
idf_generator                                                                                NaN   
epw_generator                                                                                NaN   
lab_weight                                                                              0.000000   
AGE_ERA                                                                                     1945   
TYPOLOGY                                                                             Residential   
task_id                                                     e0ea55e5-43ea-4e58-90cc-36b0fca79253   
sort_id                                                                                       35   
epw                 /usr/src/app/engine/worker/builder/shoeboxes/resources/epws/BaselineFile.epw   
actual_area                                                                          7167.848085   
end_use                                                                                            
Cooling                                                      69.141226                             
Electricity                                                 121.144549                             
Heating                                                      52.698185                             
Water                                                        39.611695                             

which                                                                                      right  
epw_scenario                                                                               rcp45  
retrofit_scenario                                                                       baseline  
schedules_scenario                                                                      baseline  
lab_scenario                                                                            baseline  
results_remote_path       EPW.rcp45_YR.2025_BLDG.NW13_RETRO.baseline_SCHED.baseline_LAB.baseline  
idf_generator                                                                                NaN  
epw_generator                                                                                NaN  
lab_weight                                                                              0.716538  
AGE_ERA                                                                                     1980  
TYPOLOGY                                                                       Lab and Mixed Use  
task_id                                                     a778d63b-c895-4319-a648-cd7f57331711  
sort_id                                                                                       73  
epw                 /usr/src/app/engine/worker/builder/shoeboxes/resources/epws/BaselineFile.epw  
actual_area                                                                          5754.141157  
end_use                                                                                           
Cooling                                                     139.009142                            
Electricity                                                 322.206243                            
Heating                                                     740.640185                            
Water                                                       105.922389

In [4]:
building_df = s.source_df.xs(2025, level="epw_year")
# building_df.to_hdf("2025_all_baselines_revised.hdf", key="data")
campus_df = building_df.sum(axis=0)  # .T.groupby(level=0).sum().T
Btu_per_kWh = 3412
# tonnes_cooling_per_Btu = 1/12000
lb_steam_per_Btu = 1 / 1199 # 200psi
kp_per_lb_steam = 1 / 1000
M_per_k = 1 / 1000
kWhth_to_kpph = Btu_per_kWh * lb_steam_per_Btu * kp_per_lb_steam
# kWth_to_cwton = Btu_per_kWh * tonnes_cooling_per_Btu
base_steamload_kpph = campus_df.Heating.mean() * kWhth_to_kpph
peak_steamload_kpph = campus_df.Heating.max() * kWhth_to_kpph
min_steamload_kpph = campus_df.Heating.min() * kWhth_to_kpph
base_elecload_MW = campus_df.Electricity.mean() * M_per_k
peak_elecload_MW = campus_df.Electricity.max() * M_per_k
min_elecload_MW = campus_df.Electricity.min() * M_per_k
# base_cwload_tons = campus_df.Cooling.mean() * kWth_to_cwton
# peak_cwload_tons = campus_df.Cooling.max() * kWth_to_cwton
# min_cwload_tons = campus_df.Cooling.min() * kWth_to_cwton

pd.DataFrame(
    [[base_steamload_kpph, peak_steamload_kpph, min_steamload_kpph], [base_elecload_MW, peak_elecload_MW, min_elecload_MW]],
    columns=["base", "peak", "min"],
    index=["steam (kpph)", "electricity (MW)"],
).round()
# df.Electricity.mean()

base   peak  min
steam (kpph)      199.0  735.0  0.0
electricity (MW)   20.0   38.0  9.0

In [30]:
lbs_per_MWh = 613
lbs_per_kpph = 158
kg_per_pound = 0.453592
end_uses = building_df.sum(axis=0).groupby(level=0).sum()
elec_emis = end_uses.Electricity * M_per_k *  lbs_per_MWh * kg_per_pound / 1000
cooling_as_elec = end_uses.Cooling / 2 * M_per_k
heating_as_kp_steam = end_uses.Heating * kWhth_to_kpph
cooling_emissions = cooling_as_elec * lbs_per_MWh * kg_per_pound / 1000
heating_emissions = heating_as_kp_steam * lbs_per_kpph  * kg_per_pound / 1000
# pd.DataFrame([[elec_emis, cooling_emissions, heating_emissions]], columns=["elec", "cooling", "heating"])
total_emiss_v1 = heating_emissions + cooling_emissions + elec_emis
mmBtu_per_MWh = 3.142
total_elec = end_uses.Electricity * M_per_k + cooling_as_elec # MWh
total_gas = heating_as_kp_steam * 153  / 114 / mmBtu_per_MWh + total_elec * 180 / 15.8 / mmBtu_per_MWh
total_emiss_v2 = total_gas * 0.180
total_emiss_v2







459096.2679525061

In [10]:
df = pd.read_hdf("c:/users/szvsw/downloads/UZB_Tashkent.384570_IWEC_office_20_South_Shading.hdf").values
df2 = pd.read_hdf("c:/users/szvsw/downloads/UZB_Tashkent.384570_IWEC_office_20_South_Shading (1).hdf").values
np.abs(df-df2).mean()


11979.673188085328

In [65]:
# fig = px.line(tl.groupby("epw_year").sum()["Total Emissions"], height=400)
# k = tl.groupby("epw_year").sum()
# kk = k["Emissions"][["Grid", "CUP"]].melt(ignore_index=False).reset_index()
# ff = px.bar(kk, x="epw_year", y="value", color="variable", height=400)
# ff.show()
kkk = tl.Emissions[["Grid","CUP"]].xs(2050, level="epw_year").melt(ignore_index=False).reset_index()
kkk = tl[ ["CUP Thermal Assignment", "District Thermal Assignment"] ].xs(2045, level="epw_year").melt(ignore_index=False).reset_index()
px.line(kkk, x="DateTime", y="value", color="variable_1",line_dash="variable_0", height=400).show()
kkk = tl[ "Electricity" ][["Final Demand"]].groupby(level="epw_year").sum().melt(ignore_index=False).reset_index()
px.line(kkk, x="epw_year", y="value", color="variable", height=400).show()
kkk = tl["Emissions"].Total.groupby(level="epw_year").sum()
px.line(kkk, height=400).show()



base   peak
steam        163.0  670.0
electricity   50.0   58.0

In [8]:
ix = s.scheduled_loads.groupby(level="epw_year").first().stack(
    level="DateTime", future_stack=True
).index
k = s.generate_nuclear_capacity(ix)
k

[0.   0.12 0.24 0.36 0.48 0.6  0.62 0.64 0.66 0.68 0.7  0.72 0.74 0.76
 0.78 0.8  0.81 0.82 0.83 0.84 0.85 0.86 0.87 0.88 0.89 0.9 ]


epw_year  DateTime           
2025      2018-01-01 00:00:00        0
          2018-01-01 01:00:00        0
          2018-01-01 02:00:00        0
          2018-01-01 03:00:00        0
          2018-01-01 04:00:00        0
                                 ...  
2050      2018-12-31 19:00:00    10000
          2018-12-31 20:00:00    10000
          2018-12-31 21:00:00    10000
          2018-12-31 22:00:00    10000
          2018-12-31 23:00:00    10000
Name: nuclear, Length: 227760, dtype: int64

In [19]:
s.source_df.xs("41", level="building_id").reset_index()["actual_area"]

0    2429.231041
1    2429.231041
2    2429.231041
3    2429.231041
Name: actual_area, dtype: float64

In [67]:
normalize = False
if normalize:
    k = (s.source_df.xs(2025,level="epw_year").T.groupby(level=0).sum().T / s.source_df.xs(2025,level="epw_year").index.to_frame()["actual_area"].values.reshape(-1,1))
else:
    k = (s.source_df.xs(2025,level="epw_year").T.groupby(level=0).sum().T )
k["total"] = k.sum(axis=1)
# k["EUI (kBtu/sqft)"] = k["EUI"] * 0.316 # convert from kWh/m2 to kBtu/sqft
k = k.sort_values("total",ascending=False).drop(columns="total").iloc[:20].melt(ignore_index=False).reset_index()
px.bar(k,x="building_id",y="value",color="end_use", labels={"variable":"end use", "value":"kWh" if not normalize else "EUI (kWh/m2)"})




c:\tools\Anaconda3\envs\mit-campus-decarbonization\lib\site-packages\plotly\express\_core.py:2065: FutureWarning:

When grouping with a length-1 list-like, you will need to pass a length-1 tuple to get_group in a future version of pandas. Pass `(name,)` instead of `name` to silence this warning.



# Plotting

In [ ]:
actual_area = (
    s.source_df.reset_index("actual_area").groupby("building_id").first()["actual_area"]
)
actual_area
a = (
    s.scheduled_loads.xs(2025, level="epw_year")
    .T.groupby("end_use")
    .sum()
    .T.reset_index("segment", drop=True)
)
fig = px.histogram(
    a.melt(ignore_index=False, value_name="energy"),
    x="energy",
    facet_col="end_use",
    facet_col_wrap=2,
    height=400,
    log_y=True,
)
# fig.show()
factor = (a.Heating / a.Cooling).rename("heating to cooling ratio")
fig = px.histogram(factor, height=400, nbins=50)
# fig.show()
fig = px.scatter(x=a.Cooling, y=factor)
# fig.show()
df = pd.concat([a, factor, actual_area], axis=1)
df
# a_eui = a /actual_area.loc[a.index].values.reshape(-1,1)
# a_eui

k = s.source_df.xs(2025, level="epw_year")
# k = k.xs(0, level="lab_weight")
k = k.T.groupby(level=0).sum().T
# data = k.xs(0, level="lab_weight")
data = k

cool_eui = pd.Series(data.Cooling.values / data.reset_index().actual_area.values, index=data.index, name="Cooling EUI")
heat_eui = pd.Series(data.Heating.values / data.reset_index().actual_area.values, index=data.index, name="Heating EUI")
elec_eui = pd.Series(data.Electricity.values / data.reset_index().actual_area.values, index=data.index, name="Electricity EUI")
water_eui = pd.Series(data.Water.values / data.reset_index().actual_area.values, index=data.index, name="Water EUI")
df = pd.concat([cool_eui, heat_eui, elec_eui, water_eui], axis=1)
df = df.melt(ignore_index=False, value_name="EUI", var_name="End Use").reset_index()
for typology in df.TYPOLOGY.unique():
    fig = px.histogram(df[df.TYPOLOGY == typology], x="EUI", facet_row="TYPOLOGY", facet_col_wrap=2, nbins=100, color="End Use", barmode="group", title=f"{typology} EUI")
    fig.show()
print("-----------------")
cool_gross = pd.Series(data.Cooling.values / 8760 / 1000, index=data.index, name="Cooling")
heat_gross = pd.Series(data.Heating.values / 8760 / 1000, index=data.index, name="Heating")
elec_gross = pd.Series(data.Electricity.values / 8760 / 1000, index=data.index, name="Electricity")
water_gross = pd.Series(data.Water.values / 8760 / 1000, index=data.index, name="Water")
df = pd.concat([cool_gross, heat_gross, elec_gross, water_gross], axis=1)
df = df.melt(ignore_index=False, value_name="Power (avg MW)", var_name="End Use").reset_index()
for typology in df.TYPOLOGY.unique():
    fig = px.histogram(df[df.TYPOLOGY == typology], x="Power (avg MW)", facet_row="TYPOLOGY", facet_col_wrap=2, nbins=100, color="End Use", barmode="group", title=f"{typology} Gross")
    fig.show()



c:\tools\Anaconda3\envs\mit-campus-decarbonization\lib\site-packages\plotly\express\_core.py:2065: FutureWarning:

When grouping with a length-1 list-like, you will need to pass a length-1 tuple to get_group in a future version of pandas. Pass `(name,)` instead of `name` to silence this warning.



-----------------


In [ ]:
data = s.source_df.xs(2025, level="epw_year")

average_power_draw = data.T.groupby(level=0).describe().T.xs("mean", level=-1)["Electricity"].sort_values(ascending=False)
max_power_draw = data.T.groupby(level=0).describe().T.xs("max", level=-1)["Electricity"].sort_values(ascending=False)
min_power_draw = data.T.groupby(level=0).describe().T.xs("min", level=-1)["Electricity"].sort_values(ascending=False)
average_power_draw.index = average_power_draw.reset_index("building_id")["building_id"]
(average_power_draw.rename("Average Power Draw (MW)").iloc[:20] / 1000).round(2)

((data.sum().groupby(level=0).describe().loc["Electricity"]).rename("Campus Wide Power Draw from lights and equip (MW)") / 1000).round(2) 




count     8.76
mean     31.38
std       5.17
min      26.25
25%      27.18
50%      28.30
75%      35.67
max      40.07
Name: Campus Wide Power Draw from lights and equip (MW), dtype: float64

In [ ]:
df = s.scheduled_loads.groupby("epw_year").sum().T.groupby(level="end_use").sum().T
annual = pd.DataFrame(df.sum(axis=1), columns=["energy"]).reset_index()
fig = px.line(annual, x="epw_year", y="energy")
fig.show()
by_end_use = df.melt(ignore_index=False, var_name="end_use", value_name="energy").reset_index()
fig = px.line(by_end_use, x="epw_year", y="energy", color="end_use")
fig.show()



c:\tools\Anaconda3\envs\mit-campus-decarbonization\lib\site-packages\plotly\express\_core.py:2065: FutureWarning:

When grouping with a length-1 list-like, you will need to pass a length-1 tuple to get_group in a future version of pandas. Pass `(name,)` instead of `name` to silence this warning.



In [74]:
k = (
    s.scheduled_loads.groupby("epw_year")
    .sum()
    .stack(level="DateTime", future_stack=True)
    .xs(2025, level="epw_year")
)
# k.Heating = k.Heating / 0.4
# k.Cooling = k.Cooling / 3.5
k = k.melt(ignore_index=False, value_name="energy", var_name="end_use").reset_index()
px.line(
    k,
    x="DateTime",
    y="energy",
    color="end_use",
)

c:\tools\Anaconda3\envs\mit-campus-decarbonization\lib\site-packages\plotly\express\_core.py:2065: FutureWarning:

When grouping with a length-1 list-like, you will need to pass a length-1 tuple to get_group in a future version of pandas. Pass `(name,)` instead of `name` to silence this warning.



In [77]:
fig = px.histogram(s.scheduled_loads["Heating"].groupby("epw_year").sum().loc[2025].values / 1000)
# set the xaxis label to "Heating Ideal Loads, hourly, MWh"
# fig.update_layout(xaxis_title="Heating Ideal Loads, hourly, MWh")
fig.show()


# Phasing

In [44]:
import boto3
from tqdm.autonotebook import tqdm
import tempfile
from concurrent.futures import ThreadPoolExecutor

bucket = "ml-for-bem"
results_path = "mit-campus-decarbonization/results"
run_name = "batch_test"
profiles_id = "fd346eec"
results_folder = f"{results_path}/{run_name}/{profiles_id}"
s3 = boto3.client("s3")

# list files in bucket using paginator
paginator = s3.get_paginator('list_objects_v2')
page_iterator = paginator.paginate(Bucket=bucket, Prefix=results_folder)

all_files = []
for page in page_iterator:
    if "Contents" in page:
        for obj in page["Contents"]:
            key = obj["Key"]
            if key.split("/")[-1].startswith("WORKER-") and key.endswith(".hdf"):
                all_files.append(key)
def download_and_open(file, local_path):
        s3.download_file(bucket, file, f"{local_path}/{Path(file).name}")
        return pd.read_hdf(f"{local_path}/{Path(file).name}")
with tempfile.TemporaryDirectory() as artifacts_dir:
    with ThreadPoolExecutor(max_workers=5) as executor:
        dfs = list(tqdm(executor.map(download_and_open, all_files, [ artifacts_dir for _ in all_files ]), total=len(all_files)))
    
all_dfs = pd.concat(dfs, keys=range(len(dfs)), names=["worker_id"])
all_dfs
all_dfs = all_dfs.set_index(pd.Series(np.arange(int(len(all_dfs)/26)).repeat(26),name="task_id"), append=True)
px.line(all_dfs.reset_index(), x="epw_year", y="Emissions", color="task_id")






  0%|          | 0/5 [00:00<?, ?it/s]

c:\tools\Anaconda3\envs\mit-campus-decarbonization\lib\site-packages\plotly\express\_core.py:2065: FutureWarning:

When grouping with a length-1 list-like, you will need to pass a length-1 tuple to get_group in a future version of pandas. Pass `(name,)` instead of `name` to silence this warning.

